# EDA & statistical inference in Python

1. Describing dataset
2. EDA: descriptive statistics for one variable
3. EDA: descriptive statistics for two (or more) variables
4. Inference: classical hypothesis testing

We can use basic statistical tools in *pandas* but *NumPy* and *SciPy* packages are more suitable for numerical descriptive statistics and hypothesis testing. We won't use any visualisation – it will be a matter of next week.

Complete tutorials:

* [pandas](https://pandas.pydata.org)
* [NumPy](https://numpy.org/doc/stable/)
* [SciPy stats](https://docs.scipy.org/doc/scipy/reference/stats.html)

*Note: **statmodels** package can be used for some statistical test, too.*

Please download `homecredit_default.zip` from the repository, extract `application_train.csv` to your working directory.

First we import necessary packages, open the data, make a random sample and select only some particular columns.

In [ ]:
# Import libraries
import pandas as pd
import numpy as np
from scipy import stats

# classes for special types
from pandas.api.types import CategoricalDtype

# Reading and adjusting data
K = pd.read_csv("application_train.csv")

# random sample of 2000 rows
K = K.sample(n=2000, axis=0)

# sample of columns
K.columns = K.columns.str.lower() # column names to lowercase
K = K[['sk_id_curr', 'target', 'name_contract_type', 'code_gender', 'cnt_children', 'amt_credit',
       'occupation_type', 'name_education_type', 'days_birth', 'own_car_age', 'ext_source_1']]

# view of the dataset
K

## 1. General analysis

The aim is to find answers to questions:

* How many rows are there? What does represent each row? Do we need any aggregation or reshaping? Are all rows useful for our purpose? Do we need to make a sample? Does each row have its unique ID?
* How many columns are there? What are their names, types, meanings?
* Are there any duplicated rows (with exclusion of ID)?
* What are counts and shares of missing values in the dataset columns?
* Are counts of missing values expectable and acceptable?
* Are any columns or rows (almost) empty and may be removed as useless?

**Summary:** What initial transformations of the dataset are useful or necessary?

In [ ]:
# count of rows and columns
print('Number of rows and columns: ', K.shape)

# column names and types
print('\nColumn names and types:\n', K.dtypes)

# Are all column names self-explanating? If not, where can I get the description?
# --> see HomeCredit_columns_description.csv

# Is there a column with ID (maybe 'sk_id_curr')?
# explore count of unique values
print('\nCount of unique values in sk_id_curr:', K[['sk_id_curr']].nunique()) # nunique method, DataFrame with one column only
print('\nCount of unique values in sk_id_curr:', len(np.unique(K['sk_id_curr']))) # other way using NumPy unique function
# number of unique values is equal to number of rows => ok, sk_id_curr can be ID

# duplicated rows?
print('\nCount of duplicated rows: ', sum(K.duplicated()))
# duplicated rows can also be assessed for subset of columns - use parameter 'subset'
print('\nCount of duplicated rows not regarding ID: ',
      sum(K.duplicated(subset=['target', 'name_contract_type', 'code_gender', 'cnt_children', 'amt_credit', 'occupation_type',
                               'name_education_type', 'days_birth', 'own_car_age', 'ext_source_1'])))

# counts of missing values
# absolute counts by column
print('\nCounts of missing values by column:\n', len(K) - K.count())
# alternative: K.isna().sum()

# relative counts (shares) by column
print('\nShare of missing values by column:\n', 1 - K.count()/len(K))
# alternative: K.isna().mean()

# how many rows have which number of non-missing values
print('\nRows by non-missing value counts:\n', K.count(axis=1).value_counts())

## 2. Distributions of individual variables

The aim is, for each column individually, to find answers to questions:

* Are values plausible?
* Are there any values standing for missing (NA), empty or other special cases?
* Is type of column appropriate for its values? Should we change it?
* How should we treat missing values?
* Numerical: How should we treat outliers? 
* Numerical: Could/should we make a binning (and if so, how)? 
* Categorial: Which categories could be joined?
* What is distribution of values? What does it mean for the problem we try to solve? 

**Summary:** In which columns should we consider fixing of values (correction, filling, replacing etc.) or transformation of them (type change, recalculating, binning etc.)? What story do data tell us? What could/should we explore more deeply?

### 2.1 Categorial variable

We make a frequency table (we combine absolute and relative frequencies).

In [ ]:
# general frequency tables by pandas - see the differences
print(K.groupby("name_education_type").size()) # output as Series, ordered by index, independent on other columns
print(K["name_education_type"].value_counts()) # output as Series, ordered by values, independent on other columns
print(K["name_education_type"].value_counts(normalize=True)) # same as previous line but as relative freqs
K.groupby("name_education_type").count() # output as DataFrame, result depends on a column (counts of non-NA - they differ!)
# conclusion: almost three quarters have a secondary education, almost one quarter has higher education

In [ ]:
# absolute and relative frequency table
freqtab = K.groupby("name_education_type").agg(count=("sk_id_curr", "count")) # absolute frequencies (counts)
freqtab["count_rel"] = freqtab["count"] / sum(freqtab["count"]) # relative frequencies
freqtab

It is reasonable to make the variable `name_education_type` ordered. Then we can compute cumulative frequencies.

In [ ]:
# making a new categorical ordered variable
cat_type = CategoricalDtype(categories=["Lower secondary", "Secondary / secondary special",
                                        "Incomplete higher", "Higher education"],
                            ordered=True)
K["education"] = K["name_education_type"].astype(cat_type)

# frequency table
freqtab = K.groupby("education").agg(count=("sk_id_curr", "count")) # absolute frequencies (counts)
freqtab["count_cum"] = freqtab["count"].cumsum() # cumulative frequencies
freqtab["count_rel"] = freqtab["count"] / sum(freqtab["count"]) # relative frequencies
freqtab["count_relcum"] = freqtab["count_rel"].cumsum() # cumulative relative frequencies
freqtab

If some categories in the variable are rare, we should consider to combine them with some others. Here is an example of such variable:

In [ ]:
K.groupby("occupation_type").agg(count=("sk_id_curr", "count")) # Many occupation types with few persons

In [ ]:
# creating a new column
# joining Cooking staff and Waiters/barmen staff to the new category Gastro
K['occupation_type2'] = K['occupation_type'].replace(['Cooking staff', 'Waiters/barmen staff'], 'Gastro')
K.groupby("occupation_type2").agg(count=("sk_id_curr", "count"))

### 2.2 Numerical variable

* min, max, mean, trimmed mean, median, quantiles
* variance, standard deviation, IQR
* skewness, kurtosis
* correlation (Pearson, Spearman)

For this type of variables, we can use both *pandas* and *NumPy/SciPy*. Let's show it on `own_car_age` variable.

**by pandas...**

Empty values (NaN) are usually ignored.

In [ ]:
# for individual column (Series)
print(K['own_car_age'].describe())

# for all numerical columns in DataFrame
K.describe()

In [ ]:
# individual statistics
print('Count of non-NA:', K['own_car_age'].count())
print('% of non-NA:', 100 * K['own_car_age'].notna().mean()) # mean of True/False = the share of True values
# alternative: print('% of non-NA:', 100 * K['own_car_age'].count() / len(K['own_car_age']))
print('Mean:', K['own_car_age'].mean())
print('Mode:', K['own_car_age'].mode().values)
print('Min:', K['own_car_age'].min())
print('Median:', K['own_car_age'].median())
print('Max:', K['own_car_age'].max())
# only one third has an own car, half of them has car older than or equal {median} years
# the most often age is {mode} years

In [ ]:
# quantiles
qtab = K['own_car_age'].quantile(q=[0.05, 0.25, 0.5, 0.75, 0.95])
print(qtab)
print('IQR:', qtab[0.75] - qtab[0.25])
# one quarter of car owners has a car of age 16+

In [ ]:
# variance and higher moments
print('Variance: ', K['own_car_age'].var()) # by default the divisor is (N-1)
print('Std. dev.: ', K['own_car_age'].std())
print('Skewness: ', K['own_car_age'].skew())
print('Kurtosis: ', K['own_car_age'].kurt())
# car age is positively skewed and has rather heavy tail

**by numpy/scipy...**

Empty values (NaN) are sometimes ignored and sometimes not. It's wise to check the documentation or simply remove them (by `.dropna` method).

In [ ]:
# basic statistics - numpy
print('Mean: ', np.mean(K['own_car_age']))
# alternatively, use np.nanmean(K['own_car_age']) or np.mean(K['own_car_age'].dropna())
print('Median: ', np.median(K['own_car_age']))
# oops, does not ingore NaNs, so use:
print('Median: ', np.nanmedian(K['own_car_age']))
# or np.median(K['own_car_age'].dropna())
print('Min: ', np.min(K['own_car_age']))
print('Max: ', np.max(K['own_car_age']))
print('Quantiles: ', np.nanquantile(K['own_car_age'], q=[0.05, 0.25, 0.5, 0.75, 0.95]))
# for mode, use SciPy (see next cell)
print('Variance: ', np.var(K['own_car_age'])) # by default the divisor is N
print('Std. dev.: ', np.std(K['own_car_age']))

In [ ]:
# advanced statistics - scipy
print('Mode:', stats.mode(K['own_car_age'].dropna()))
print('Trimmed mean (5+5 % margins off):', stats.trim_mean(K['own_car_age'].dropna(), 0.05))
# there are other trimmed statistics too
print('IQR:', stats.iqr(K['own_car_age'].dropna()))
# trimmed min, max, var, std are available, too
print('Skewness:', stats.skew(K['own_car_age'].dropna()))
print('Kurtosis:', stats.kurtosis(K['own_car_age'].dropna()))
# skewness and kurtosis are slightly different compared to pandas

It's possible to calculate frequencies in bins (intervals) or even to convert the variable to categorial (make a binning). There are methods to do it both in pandas and in NumPy.

In [ ]:
# pandas - without modification of the dataset
print(pd.cut(K['own_car_age'], bins=[0, 5, 10, 20, 100], include_lowest=True).value_counts())
K.assign(own_car_age_cat = pd.cut(K['own_car_age'], bins=[0, 5, 10, 20, 100], include_lowest=True)) \
    .groupby('own_car_age_cat') \
    .agg(count=("sk_id_curr", "count"))

In [ ]:
# with a new (labeled) column
K['own_car_age_cat'] = pd.cut(K['own_car_age'], bins=[0, 5, 10, 20, 100],
                              include_lowest=True,
                              labels=['0-5', '6-10', '11-20', 'above 20'])
K.groupby('own_car_age_cat').agg(count=("sk_id_curr", "count"))

In [ ]:
# numpy - use histogram
print(np.histogram(K['own_car_age'], bins=[0, 5, 10, 20, 100])[0])
# !!! all bins but the last are right-open, i. e. [a, b)

# for discrete and small non-negative values, one may use np.bincount
# can be combined with np.digitize (binning and indexing):
print(np.bincount(np.digitize(K['own_car_age'].dropna(), bins=[0, 5, 10, 20, 100])))

In [ ]:
# scipy - generalization of binning/histogram
# see function binned_statistic
# following line works like np.histogram
stats.binned_statistic(K['own_car_age'], K['own_car_age'], 'count', [0, 5, 10, 20, 100])[0]

## 3. Relationships of variables

The basic question is: are these variables independent or is there any relationship between them? (If so, is it expected or surprising?) 

Method for analysis are different depending on type (categorial or numerical) of both variables. 

* If one of variables is categorial, the basic strategy is to split the data into categories by this variable and to study statistics of the other variable for each category.
* If both variables are numerical, then we compute statistics like correlation.
* For a numerical variable, one may consider binning it and getting this way a categorial variable.

### 3.1 Categorial vs. categorial

In this case we usually compute a contingency table (2-D frequency table).

In [ ]:
# contingency table with absolute frequencies
pd.crosstab(K["education"], K["code_gender"])

In [ ]:
# for relative frequencies in contingency table, use parameter normalize:
pd.crosstab(K["education"], K["code_gender"], normalize="columns") # relative by columns
# only slight differences in shares between men and women
# should be compared to all population - is it expectable?

In [ ]:
# frequency table in long format
print(K.groupby(["education", "code_gender"]).size())
K.groupby(["education", "code_gender"]).agg(count=("sk_id_curr", "count"))

### 3.2 Categorial vs. numerical

We can split the data by categorial variable and compute statistics by categories, e. g. mean, median or SD, and compare them. Computing is easy by *pandas groupby* and *agg* methods.

In [ ]:
# pandas - groupby + aggregation
# it is possible to use user defined functions
def iqr(x): # interquartile range
    return x.quantile(q=0.75)-x.quantile(q=0.25)

K.groupby("code_gender").agg({"own_car_age": ["count", "mean", "median", "std", "max", "min", iqr]})
# women have a bit bigger variance (std. dev.) of car age, probably they have also newer cars more often than men

Or one may consider to categorize (bin) the numerical variable and transform it to **Categorial vs. categorial** case.

### 3.3 Numerical vs. numerical

The basic statistics for this case is a correlation coefficient.

In [ ]:
# correlation between two columns - pandas
print("Correlation (Pearson): ", K["days_birth"].corr(K["amt_credit"]))
print("Correlation (Pearson): ", K["days_birth"].corr(K["amt_credit"], method='spearman'))

# correlation matrix between every pair of numerical variables
corrmat = K.corr(numeric_only=True)
corrmat

# target has low correlation with ext_source_1 and age (days_birth)
# moderate positive correlation of age and cnt_children

In [ ]:
# correlation - scipy
print('Correlation (Pearson):', stats.pearsonr(K['days_birth'], K['amt_credit'])) # with test (H0: zero correlation)
print('Correlation (Spearman):', stats.spearmanr(K['days_birth'], K['amt_credit']))
# borderly accepted that amount and age may be uncorrelated

## 4. Classical hypothesis testing

* t-tests, F-test
* non-parametric (Wilcoxon, Mann-Whitney)
* goodness-of-fit tests (normality test, chi-square test for contingency tables)
* correlation test - in *scipy* is a part of correlation computing, see above
* one-way ANOVA

In [ ]:
# for better understanding, we create a new column age
K['age'] = -K['days_birth']/365.25

In [ ]:
# t-test
# one sample: is mean age of applicants generally equal 40 years?
test_result = stats.ttest_1samp(K['age'], 40, nan_policy='omit')
print(test_result) # rejected
print(test_result.confidence_interval()) # conf. interval for population mean

In [ ]:
# two sample: is mean age of applying women same as of men?
test_result = stats.ttest_ind(K[K['code_gender']=='F']['age'], K[K['code_gender']=='M']['age'],
                              nan_policy='omit')
# for not equal variances, add equal_var=False
print(test_result) # rejected
print(test_result.confidence_interval()) # conf. interval for mean difference

In [ ]:
# nonparametric alternatives: Mann-Whitney for two sample, Wilcoxon for one sample
test_result = stats.mannwhitneyu(K[K['code_gender']=='F']['age'], K[K['code_gender']=='M']['age'],
                                 nan_policy='omit')
print(test_result) # rejected

In [ ]:
# equal variance tests
# are variances of men's and women's age equal?

In [ ]:
# F-test has no straightforward implementation
# Calculate the sample variances
variance1 = np.var(K[K['code_gender']=='F']['age'], ddof=1) # by default the divisor is N (ddof=0)
variance2 = np.var(K[K['code_gender']=='M']['age'], ddof=1)
 
# Calculate the F-statistic
f_value = variance1 / variance2
 
# Calculate the degrees of freedom
df1 = K[K['code_gender']=='F']['age'].count() - 1
df2 = K[K['code_gender']=='M']['age'].count() - 1
 
# Calculate the p-value
p_value = stats.f.cdf(f_value, df1, df2)
 
# Print the results
print('Degree of freedom 1:',df1)
print('Degree of freedom 2:',df2)
print("F-statistic:", f_value)
print("p-value:", p_value)
# accepted

In [ ]:
# alternatives
# Bartlett test (requires normality)
test_result = stats.bartlett(K[K['code_gender']=='F']['age'], K[K['code_gender']=='M']['age'])
print(test_result) # accepted
# Levene test
test_result = stats.levene(K[K['code_gender']=='F']['age'], K[K['code_gender']=='M']['age'])
print(test_result) # tight rejection

# other test: fligner (non-parametric)

In [ ]:
# normality test
# is the distribution of applicants' age normal?
test_result = stats.normaltest(K['age'], nan_policy='omit')
print(test_result) # rejected

test_result = stats.shapiro(K['age'])
print(test_result) # rejected

# other tests: anderson, kstest

In [ ]:
# chi-squared test
# one-way example
test_result = stats.chisquare([16, 18, 16, 14, 12, 12], f_exp=[16, 16, 16, 16, 16, 8])
print(test_result) # accepted that observed do not deviate from expected

# contingency table
test_result = stats.chi2_contingency(pd.crosstab(K["education"], K["code_gender"]))
print(test_result) # accepted that rows and columns may be independent

In [ ]:
# one-way ANOVA
# is mean amount same for applicants with different education?
test_result = stats.f_oneway(K[K['education']=='Lower secondary']['amt_credit'],
                             K[K['education']=='Secondary / secondary special']['amt_credit'],
                             K[K['education']=='Incomplete higher']['amt_credit'],
                             K[K['education']=='Higher education']['amt_credit'])
print(test_result) # rejected

# non-parametric alternative
test_result = stats.kruskal(K[K['education']=='Lower secondary']['amt_credit'],
                            K[K['education']=='Secondary / secondary special']['amt_credit'],
                            K[K['education']=='Incomplete higher']['amt_credit'],
                            K[K['education']=='Higher education']['amt_credit'],
                            nan_policy='omit')
print(test_result) # rejected

# post-hoc test Tukey HSD
test_result = stats.tukey_hsd(K[K['education']=='Lower secondary']['amt_credit'],
                              K[K['education']=='Secondary / secondary special']['amt_credit'],
                              K[K['education']=='Incomplete higher']['amt_credit'],
                              K[K['education']=='Higher education']['amt_credit'])
print(test_result)
# the only significant difference is between Secondary and Higher